# Non-convex optimization - application to matrix completion
In this notebook, we define matrix completion problems and we implement a (naive) algorithm to solve it through non-convex optimization.

In [ ]:
from enum import Enum
import numpy as np
from numpy import random
import matplotlib.pyplot as plt

## Matrix completion
Matrix completion is the problem of recovering a matrix $M\in \mathbb{R}^{n\times m}$ from the observation of a subset of entries, $(M_{i,j})_{(i,j)\in S}$ for some $S\subset\{1,\dots,n\}\times\{1,\dots,m\}$, under the hypothesis that $M$ has low rank.

In this notebook, we make a simplifying assumption: $M$ is square ($n=m$) and positive semidefinite ($M\succeq 0$).

To perform tests, we will need to generate random instances of matrix completion problems. This is done with two functions. The first one, subsample_matrix, selects a random subset of entries of a matrix.

In [ ]:
def subsample_matrix(M,s):
    # M is the matrix to subsample
    # s is the number of entries to select
    m = np.shape(M)[0]
    n = np.shape(M)[1]
    subset = random.choice(m*n,s,replace=False)
    mask = np.zeros(n*m)
    mask[subset] = 1
    mask = mask.reshape((m,n))
    M_sub = M * mask
    return (M_sub,mask)

**Question 1:** Write a function generate_matrix(n,p) which returns a random $n\times n$ semidefinite positive matrix with rank $p$.

In [ ]:
def generate_matrix(n,p):
    # n is the dimension of the matrix
    # p is the rank
    ## Insert your code.

## Cost function and gradient descent

Given the rank $p$ and the entries $(M_{i,j})_{(i,j)\in S}$, we attempt to reconstruct $M$ with a naive heuristic.

**Question 2:** Show that $M$ is semidefinite positive with rank at most $p$ if and only if it can be written as $M=UU^T$ for some $U\in\mathbb{R}^{n\times p}$.

This property implies that, to recover $M$, it is enough to find $U\in\mathbb{R}^{n\times p}$ such that, for all $(i,j)\in S$, $(UU^T)_{i,j} = M_{i,j}$.

**Question 3:** Show that the matrices $U$ which satisfy these equalities are exactly the minimizers of the following function:
\begin{equation*}
L : U\in\mathbb{R}^{n\times p} \to \sum_{(i,j)\in S} ((UU^T)_{i,j}-M_{i,j})^2.
\end{equation*}

This suggests to recover $U$ by attempting to find a minimizer of $L$. We do this by running gradient descent on $L$.

**Question 4:** Show that, for any $U\in\mathbb{R}^{n\times p}$,
\begin{equation*}
\nabla L(U) = 2 (E+E^T)U,\mbox{ with }E = (UU^T-M) \otimes \mathrm{Mask},
\end{equation*}
where $\mathrm{Mask}$ is the $n\times n$ matrix such that
\begin{align*}
\mathrm{Mask}_{i,j}&=1\mbox{ if }(i,j)\in S,\\
&=0\mbox{ otherwise},
\end{align*}
and $\otimes$ denotes the coordinate by coordinate multiplication.

**Question 5:** Implement functions cost_function($U$,$M_{sub}$,$\mathrm{Mask}$) and cost_and_gradient($U$,$M_{sub}$,$\mathrm{Mask}$), which respectiverly compute $L(U)$ and $(L(U),\nabla L(U))$.

In [ ]:
def cost_function(U,M_sub,mask):
    # M_sub,mask are the observed values and their position
    # U is the point at which L and its gradient are computed
    ## Insert your code

In [ ]:
def cost_and_gradient(U,M_sub,mask):
    # M_sub,mask are the observed values and their position
    # U is the point at which L and its gradient are computed
    ## Insert your code
    return (cost,grad)

We define a function classify which, given a matrix $U$, determines whether it is an approximate global minimum of $L$, an approximate first-order critical point, or neither of them.

In [ ]:
class convergence(Enum):
    NOT_CONVERGED = 0
    GLOBAL_MINIMUM = 1
    CRITICAL_POINT = 2

In [ ]:
def classify(M_sub,U,cost,grad):
    # M_sub,mask are the observed values and their position
    # U is the candidate solution
    
    if cost/np.sum(M_sub**2)<1e-4:
        return convergence.GLOBAL_MINIMUM # solution
    elif np.linalg.norm(grad)/np.linalg.norm(U)<1e-3:
        return convergence.CRITICAL_POINT # first order critical
    else:
        return convergence.NOT_CONVERGED # not converged

Properly choosing the stepsize of gradient descent is delicate. We propose to use backtracking line search. The following function implements it. It takes as input the previous stepsize (as well as the parameters of the problem, the current iterate, and the value and gradient of $L$ at this iterate) and returns the new one.

In [ ]:
def backtrack(previous_step,M_sub,mask,U,cost,grad):
    # previous_step is the step used at the previous iteration, or the initial one
    # M_sub,mask are the observed values and their position
    # U is the current iterate
    # cost,grad are the value and gradient of L at U
    step = 1.1*previous_step
    norm_grad_square = np.sum(grad**2)
    while (cost_function(U-step*grad,M_sub,mask)-cost > 
          - step * norm_grad_square / 2):
        step = step/2
    return step

**Question 6:** Write a function gradient_descent_solver($M_{sub}$,$\mathrm{mask}$,$p$,nb_its) which tries to reconstruct $M$ by performing nb_its gradient descent steps on $L$, starting from a random initial point. The function must return the candidate solution $M$, the list of values of $L$ explored during the descent and the convergence status after the last iteration, as defined by the function classify.

To save time, interrupt the descent before reaching nb_its iterations if approximate convergence has already occured (use the function classify again).

In [ ]:
def gradient_descent_solver(M_sub,mask,p,nb_its):
    # M_sub, mask are the observed values and their position
    # p is the rank
    # nb_its is the number of descent steps
    ## Insert your code
    return (M_final,error,status)

## Tests

We first test the code by running a simple example.

In [ ]:
n = 5
p = 2
s = 13
# Generate random instance
M_sol = generate_matrix(n,p)
(M_sub,mask) = subsample_matrix(M_sol,s)
# Run gradient descent
(M,error,status) = gradient_descent_solver(M_sub,mask,p,10000)
# Plot the results
print status
plt.figure(1)
plt.plot(np.arange(10,np.size(error)),error[10:])
plt.xlabel('iteration')
plt.ylabel('$L$')
plt.figure(2)
plt.subplot(221)
plt.title('Ground truth')
plt.imshow(M_sol)
plt.subplot(222)
plt.title('Candidate solution')
plt.imshow(M,vmin=np.amin(M_sol),vmax=np.amax(M_sol))
plt.subplot(223)
plt.title('Difference')
plt.imshow(M-M_sol,vmin=np.amin(M_sol),vmax=np.amax(M_sol))
plt.subplot(224)
plt.title('Mask')
plt.imshow(mask)

Secondly, we study the influence of the number of observed values on the behavior of gradient descent.

In [ ]:
def test(n,p,s,nb_its,nb_tests):
    # (n,p,s) = (matrix size, rank, number of observed values)
    # nb_its is the number of gradient descent steps
    # nb_tests is the number of tests
    counter = [0,0,0]
    for n_it in range(0,nb_tests):
        M = generate_matrix(n,p)
        (M_sub,mask) = subsample_matrix(M,s)
        (U,error,status) = gradient_descent_solver(M_sub,mask,p,nb_its)
        counter[status.value] = counter[status.value] + 1
    return counter

In [ ]:
n = 9
p = 1
vals_s = range(10,40,2)
nb_s = len(vals_s)
counter = np.zeros((nb_s,3))
print('s = '),
for n_it in range(0,nb_s):
    s = vals_s[n_it]
    print(str(s) + ' - '),
    counter[n_it,:] = test(n,p,s,20000,50)
plt.xlabel('s')
plt.ylabel('counts')
plt.plot(vals_s,counter[:,convergence.GLOBAL_MINIMUM.value],label='Global minimum')
plt.plot(vals_s,counter[:,convergence.CRITICAL_POINT.value],label='Critical point')
plt.plot(vals_s,counter[:,convergence.NOT_CONVERGED.value],label='Not converged')
plt.legend()

## Additional questions

<ul>
<li>Perform tests for other values of $n,p$. How does the behavior of the algorithm vary with these parameters?</li>
<li>Play with the stepsize.</li>
<li>Implement an other optimization algorithm than gradient descent.</li>
<li>Show that, for any $U\in\mathbb{R}^{n\times p},G\in O(p)$, $L(UG)=L(U)$.</li>
<li>Compute all the critical points of $L$ when $s=n^2$. Is it in accordance with what you observe numerically? If not, why?</li>
<li>Same question when $s=1$.</li>
</ul>